<a target="_blank" href="https://colab.research.google.com/github/UpstageAI/cookbook/blob/main/cookbooks/upstage/Solar-Full-Stack LLM-101/05_3_OracleDB.ipynb">
<img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/>
</a>

# Try2 - 아래 순서 중 1번을 MMLU로, 2번은 MMLU이므로 쪼갤 필요 없고, 3번 samples 그대로 넣고, 4번은 splits 고를 필요 없이 전체 중 retrieve(검색)해서 답변 생성
1. pdf 넣기, 로드 2. 쪼개서 splits 3. samples로 prompts:answers 페어 만들기 4. prompts 기반으로 splits(KB)에서 필요한 부분을 검색하여 response 생성 5. match로 response 형식 변경

# Try2 목적: KB를 ewha pdf가 아니라 MMLU로 넣었을 때 얼마나 acc 나오는지 확인하고자 함. => acc 60% 나왔음.

In [11]:
!pip3 install datasets

from datasets import load_dataset

# MMLU Pro 데이터셋 로드
dataset = load_dataset("TIGER-Lab/MMLU-Pro", split="test")

# 데이터셋 확인 (각 항목에 대한 질문과 답변)
print(dataset[0])  # 첫 번째 항목 보기

{'question_id': 70, 'question': 'Typical advertising regulatory bodies suggest, for example that adverts must not: encourage _________, cause unnecessary ________ or _____, and must not cause _______ offence.', 'options': ['Safe practices, Fear, Jealousy, Trivial', 'Unsafe practices, Distress, Joy, Trivial', 'Safe practices, Wants, Jealousy, Trivial', 'Safe practices, Distress, Fear, Trivial', 'Unsafe practices, Wants, Jealousy, Serious', 'Safe practices, Distress, Jealousy, Serious', 'Safe practices, Wants, Fear, Serious', 'Unsafe practices, Wants, Fear, Trivial', 'Unsafe practices, Distress, Fear, Serious'], 'answer': 'I', 'answer_index': 8, 'cot_content': '', 'category': 'business', 'src': 'ori_mmlu-business_ethics'}


In [12]:
!pip3 install -qU python-dotenv PyPDF2 langchain langchain-community langchain-core langchain-text-splitters langchain_upstage oracledb python-dotenv``

In [ ]:
# set parameters

api_key = "키"
data_path = "경로"

In [32]:
print(dataset[0]) 

{'question_id': 70, 'question': 'Typical advertising regulatory bodies suggest, for example that adverts must not: encourage _________, cause unnecessary ________ or _____, and must not cause _______ offence.', 'options': ['Safe practices, Fear, Jealousy, Trivial', 'Unsafe practices, Distress, Joy, Trivial', 'Safe practices, Wants, Jealousy, Trivial', 'Safe practices, Distress, Fear, Trivial', 'Unsafe practices, Wants, Jealousy, Serious', 'Safe practices, Distress, Jealousy, Serious', 'Safe practices, Wants, Fear, Serious', 'Unsafe practices, Wants, Fear, Trivial', 'Unsafe practices, Distress, Fear, Serious'], 'answer': 'I', 'answer_index': 8, 'cot_content': '', 'category': 'business', 'src': 'ori_mmlu-business_ethics'}


In [33]:
from langchain_upstage import UpstageLayoutAnalysisLoader
from langchain.schema import Document
import os


# 데이터를 Document 형식으로 변환
documents = [
    Document(
        page_content=item['question'],
        metadata={
            "options": item['options'],
            "answer": item['answer'],
            "category": item['category']
        }
    )
    for item in dataset
]


In [34]:
print(documents)

[Document(metadata={'options': ['Safe practices, Fear, Jealousy, Trivial', 'Unsafe practices, Distress, Joy, Trivial', 'Safe practices, Wants, Jealousy, Trivial', 'Safe practices, Distress, Fear, Trivial', 'Unsafe practices, Wants, Jealousy, Serious', 'Safe practices, Distress, Jealousy, Serious', 'Safe practices, Wants, Fear, Serious', 'Unsafe practices, Wants, Fear, Trivial', 'Unsafe practices, Distress, Fear, Serious'], 'answer': 'I', 'category': 'business'}, page_content='Typical advertising regulatory bodies suggest, for example that adverts must not: encourage _________, cause unnecessary ________ or _____, and must not cause _______ offence.'), Document(metadata={'options': ['Shareholders, Diligence, Self-interest', 'Shareholders, Self-interest, Care and Skill', 'Stakeholders, Care and skill, Self-interest', 'Stakeholders, Diligence, Care and Skill', 'Customers, Care and Skill, Diligence', 'Shareholders, Care and Skill, Diligence', 'Shareholders, Self-interest, Diligence', 'Empl

In [16]:
!pip3 install pandas

In [17]:
# read samples.csv file

import pandas as pd

def read_data(data_path):
    data = pd.read_csv(data_path)
    prompts = data['prompts']
    answers = data['answers']
    # returns two lists: prompts and answers
    return prompts, answers

In [18]:
prompts, answers = read_data(os.path.join(data_path, 'samples.csv'))

In [43]:
# 필수 라이브러리 설치
!pip3 install langchain-openai langchain_upstage langchain-core langchain-text-splitters transformers pandas datasets faiss-cpu

In [ ]:
from langchain.vectorstores import FAISS
from langchain.embeddings import OpenAIEmbeddings
from langchain_openai import OpenAI
from langchain.chains import create_retrieval_chain
from langchain.chains import RetrievalQA

# Upstage API 키 설정
os.environ["OPENAI_API_KEY"] = "키"

# MMLU Pro 데이터셋에서 문서를 벡터화하여 리트리버 준비
from langchain.embeddings.openai import OpenAIEmbeddings

# OpenAI Embeddings 생성
embeddings = OpenAIEmbeddings()

# FAISS 인덱스를 생성
faiss_index = FAISS.from_documents(documents, embeddings)

# LLM 및 리트리버 준비
llm = OpenAI(temperature=0)  # 필요 시 파라미터 설정
retriever = faiss_index.as_retriever()

# QA 체인 생성
qa_chain = RetrievalQA.from_chain_type(
    llm=llm,
    retriever=retriever,
)

In [46]:
# 질문에 대해 리트리버로 검색하여 답변 생성
responses = []
for prompt in prompts:
    response = qa_chain.run(prompt)
    responses.append(response)

/var/folders/1p/w6hpd8395gdb7ybzk5dvbcsw0000gn/T/ipykernel_23725/2251826334.py:4: LangChainDeprecationWarning: The method `Chain.run` was deprecated in langchain 0.1.0 and will be removed in 1.0. Use :meth:`~invoke` instead.
  response = qa_chain.run(prompt)


In [47]:
for i in responses:
    print(i)
    print('-'*10)



(A) 인정 안됨
----------
 (D) 임의 지정된 숫자
----------
 (A) 컴퓨터, 카메라, 마이크
----------

(C) 학기 초
----------
 (B) 최소 80% 수업 시청
----------
 (C) a prescription of how we should treat nonhuman animals.
----------

(F) 19.8%
----------

(I) promoting the principles of the free enterprise system
----------

(J) Natural Law
----------

(C) Baron Montesquieu
----------


In [50]:
# funcion to extract an answer from response

import re

def extract_answer(response):
    """
    extracts the answer from the response using a regular expression.
    expected format: "[ANSWER]: (A) convolutional networks"

    if there are any answers formatted like the format, it returns None.
    """
    pattern = r"\[ANSWER\]:\s*\((A|B|C|D|E)\)"  # Regular expression to capture the answer letter and text
    match = re.search(pattern, response)

    if match:
        return match.group(1) # Extract the letter inside parentheses (e.g., A)
    else:
        return extract_again(response)

def extract_again(response):
    pattern = r"\b[A-J]\b(?!.*\b[A-J]\b)"
    match = re.search(pattern, response)
    if match:
        return match.group(0)
    else:
        return None

In [51]:
# print accuracy

cnt = 0

for answer, response in zip(answers, responses):
    print("-"*10)
    generated_answer = extract_answer(response)
    print(response)
    # check
    if generated_answer:
        print(f"generated answer: {generated_answer}, answer: {answer}")
    else:
        print("extraction fail")


    if generated_answer == None:
        continue
    if generated_answer in answer:
        cnt += 1

print()
print(f"acc: {(cnt/len(answers))*100}%")

----------

(A) 인정 안됨
generated answer: A, answer: (A)
----------
 (D) 임의 지정된 숫자
generated answer: D, answer: (B)
----------
 (A) 컴퓨터, 카메라, 마이크
generated answer: A, answer: (A)
----------

(C) 학기 초
generated answer: C, answer: (B)
----------
 (B) 최소 80% 수업 시청
generated answer: B, answer: (B)
----------
 (C) a prescription of how we should treat nonhuman animals.
generated answer: C, answer: (E)
----------

(F) 19.8%
generated answer: F, answer: (J)
----------

(I) promoting the principles of the free enterprise system
generated answer: I, answer: (I)
----------

(J) Natural Law
generated answer: J, answer: (J)
----------

(C) Baron Montesquieu
generated answer: C, answer: (C)

acc: 60.0%
